In [1]:
# Collaborative Filtering : User similarity based recommendation
## 1) Get similarities of between all users (using Similarity measures)
## 2) Get similarities between current user and others
## 3) Get estimated rating of items which current user do not rate yet
## 4) Recommend N items ranked high

# Similarity measure
# 1) Correlations
# 2) Cosine similarity : simil(x,y) = /sum_i{r_{x,i}*r_{y,i}}/(/sqrt{/sum_i{r_{x,i}**2}}*/sqrt{/sum_i{r_{y,i}**2}})
# 3) Tanimoto coefficient (Binary data) : simil(x,y) = c/(a+b-c) 
# 4) Jaccard coefficeint (Binary data)
# 5) Pearson correlation coefficient

In [2]:
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.model_selection import train_test_split
import pandas as pd
import numpy as np

In [3]:
# data directory absolute path
data_dir = '../../../../data/'

# Read data
u_cols = ['user_id', 'age', 'sex', 'occupation', 'zip_code']
users = pd.read_csv(data_dir+'u.user', sep='|', names=u_cols, encoding='latin-1')

i_cols = ['movie_id', 'title', 'release date', 'video release date', 'IMDB URL', 
          'unknown', 'Action', 'Adventure', 'Animation', 'Childeren\'s', 'Comedy', 'Crime', 'Documentary', 'Drama',
          'Fantasy', 'Film-Noir', 'Horror', 'Musical', 'Mystery', 'Romance', 'Sci-Fi', 'Thriller', 'War', 'Western'
         ]
movies = pd.read_csv(data_dir+'u.item', sep='|', names=i_cols, encoding='latin-1')

r_cols = ['user_id', 'movie_id', 'rating', 'timestamp']
ratings = pd.read_csv(data_dir+'u.data', sep='\t', names=r_cols, encoding='latin-1')

# timestamp 제거 
ratings = ratings.drop('timestamp', axis=1)
# movie ID와 title 빼고 다른 데이터 제거
movies = movies[['movie_id', 'title']]

### User-Item Matrix

In [4]:
x = ratings.copy()
y = ratings['user_id']
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.25, stratify=y)

def RMSE(y_true, y_pred):
    return np.sqrt(np.mean((np.array(y_true) - np.array(y_pred))**2))

def score(model):
    id_pairs = zip(x_test['user_id'], x_test['movie_id'])
    y_pred = np.array([model(user, movie) for (user, movie) in id_pairs])
    y_true = np.array(x_test['rating'])
    return RMSE(y_true, y_pred)

rating_matrix = x_train.pivot(index='user_id', columns='movie_id', values='rating')
# print(x_train)
# print(rating_matrix)

### User-User Similarity Matrix 

In [5]:
# get cosine similarities of all user in train set
dummy_matrix = rating_matrix.copy().fillna(0)
user_similarity = cosine_similarity(dummy_matrix, dummy_matrix)
user_similarity = pd.DataFrame(user_similarity, index=rating_matrix.index, columns=rating_matrix.index)
print('User similirarity matrix')
user_similarity

User similirarity matrix


user_id       1         2         3         4         5         6         7    \
user_id                                                                         
1        1.000000  0.118312  0.061681  0.063981  0.344457  0.280803  0.331241   
2        0.118312  1.000000  0.088426  0.031997  0.030740  0.168398  0.094577   
3        0.061681  0.088426  1.000000  0.243208  0.000000  0.053641  0.056746   
4        0.063981  0.031997  0.243208  1.000000  0.014079  0.030139  0.041049   
5        0.344457  0.030740  0.000000  0.014079  1.000000  0.141397  0.230803   
...           ...       ...       ...       ...       ...       ...       ...   
939      0.075165  0.220459  0.000000  0.000000  0.036508  0.085022  0.095023   
940      0.251427  0.109605  0.135164  0.095837  0.179032  0.274800  0.248275   
941      0.086492  0.139573  0.109560  0.063137  0.073114  0.111966  0.045047   
942      0.139306  0.201950  0.102455  0.117721  0.087517  0.287458  0.212895   
943      0.279126  0.060324  0.020717  0.037606  0.181800  0.219741  0.286451   

user_id       8         9         10   ...       934       935       936  \
user_id                                ...                                 
1        0.226088  0.036442  0.278568  ...  0.271851  0.064993  0.188502   
2        0.060954  0.218695  0.053544  ...  0.090760  0.301760  0.287337   
3        0.035050  0.084117  0.049035  ...  0.009684  0.059218  0.133330   
4        0.082815  0.000000  0.039806  ...  0.015067  0.000000  0.065728   
5        0.161136  0.008019  0.189510  ...  0.208085  0.015807  0.048629   
...           ...       ...       ...  ...       ...       ...       ...   
939      0.067340  0.051946  0.033178  ...  0.066139  0.348141  0.249262   
940      0.237058  0.080060  0.281496  ...  0.275658  0.040350  0.115135   
941      0.060837  0.080913  0.083834  ...  0.013041  0.135569  0.177774   
942      0.190143  0.102253  0.171302  ...  0.160747  0.048187  0.077342   
943      0.236520  0.061964  0.144136  ...  0.170328  0.108571  0.108308   

user_id       937       938       939       940       941       942       943  
user_id                                                                        
1        0.098801  0.120269  0.075165  0.251427  0.086492  0.139306  0.279126  
2        0.361735  0.209454  0.220459  0.109605  0.139573  0.201950  0.060324  
3        0.086305  0.064520  0.000000  0.135164  0.109560  0.102455  0.020717  
4        0.054257  0.025323  0.000000  0.095837  0.063137  0.117721  0.037606  
5        0.055850  0.070753  0.036508  0.179032  0.073114  0.087517  0.181800  
...           ...       ...       ...       ...       ...       ...       ...  
939      0.198977  0.296696  1.000000  0.023667  0.052623  0.000000  0.113733  
940      0.114050  0.084493  0.023667  1.000000  0.027649  0.201437  0.159980  
941      0.216953  0.195378  0.052623  0.027649  1.000000  0.095095  0.104619  
942      0.141552  0.059353  0.000000  0.201437  0.095095  1.000000  0.153164  
943      0.081514  0.147065  0.113733  0.159980  0.104619  0.153164  1.000000  

[943 rows x 943 columns]

In [6]:
def simple_cf(user_id, movie_id):
    if movie_id in rating_matrix:
        sim_scores = user_similarity[user_id].copy() # get similarity from user-user matrix
        movie_ratings = rating_matrix[movie_id].copy() # get rating from user-item matrix
        print(user_id, movie_id)
        print(movie_ratings)
        none_rating_idx = movie_ratings[movie_ratings.isnull()].index # list
        movie_ratings = movie_ratings.dropna()
        sim_scores = sim_scores.drop(none_rating_idx)
        mean_rating = np.dot(sim_scores, movie_ratings) / sim_scores.sum()
    else:
        mean_rating = 3.0
    
    return mean_rating

score(simple_cf)

671 123
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 123, Length: 943, dtype: float64
312 482
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 482, Length: 943, dtype: float64
701 328
user_id
1      NaN
2      NaN
3      NaN
4      3.0
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    3.0
943    NaN
Name: 328, Length: 943, dtype: float64
261 410
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      1.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 410, Length: 943, dtype: float64
23 1
user_id
1      5.0
2      4.0
3      NaN
4      NaN
5      4.0
      ... 
939    NaN
940    NaN
941    5.0
942    NaN
943    NaN
Name: 1, Length: 943, dtype: float64
194 198
user_id
1      5.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN

736 532
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 532, Length: 943, dtype: float64
95 142
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 142, Length: 943, dtype: float64
851 127
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    5.0
940    NaN
941    NaN
942    NaN
943    5.0
Name: 127, Length: 943, dtype: float64
303 282
user_id
1      NaN
2      4.0
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    5.0
943    5.0
Name: 282, Length: 943, dtype: float64
44 603
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 603, Length: 943, dtype: float64
144 297
user_id
1      NaN
2      4.0
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 297, Length:

58 1106
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 1106, Length: 943, dtype: float64
870 47
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    3.0
941    NaN
942    NaN
943    NaN
Name: 47, Length: 943, dtype: float64
689 471
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    4.0
941    NaN
942    NaN
943    5.0
Name: 471, Length: 943, dtype: float64
533 475
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    4.0
942    NaN
943    5.0
Name: 475, Length: 943, dtype: float64
864 102
user_id
1      2.0
2      NaN
3      NaN
4      NaN
5      3.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 102, Length: 943, dtype: float64
222 672
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943   

404 323
user_id
1      NaN
2      NaN
3      2.0
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 323, Length: 943, dtype: float64
13 302
user_id
1      NaN
2      NaN
3      2.0
4      NaN
5      NaN
      ... 
939    NaN
940    4.0
941    NaN
942    NaN
943    NaN
Name: 302, Length: 943, dtype: float64
405 577
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 577, Length: 943, dtype: float64
269 488
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 488, Length: 943, dtype: float64
385 1135
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 1135, Length: 943, dtype: float64
243 86
user_id
1      5.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 86, Length

406 565
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 565, Length: 943, dtype: float64
432 121
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    5.0
940    NaN
941    NaN
942    NaN
943    NaN
Name: 121, Length: 943, dtype: float64
308 322
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    3.0
943    NaN
Name: 322, Length: 943, dtype: float64
707 197
user_id
1      5.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 197, Length: 943, dtype: float64
148 214
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 214, Length: 943, dtype: float64
422 7
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    4.0
941    NaN
942    NaN
943    

...

648 167
user_id
1      2.0
2      NaN
3      NaN
4      NaN
5      2.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 167, Length: 943, dtype: float64
638 679
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 679, Length: 943, dtype: float64
758 302
user_id
1      NaN
2      NaN
3      2.0
4      NaN
5      NaN
      ... 
939    NaN
940    4.0
941    NaN
942    NaN
943    NaN
Name: 302, Length: 943, dtype: float64
775 310
user_id
1      NaN
2      4.0
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    4.0
943    NaN
Name: 310, Length: 943, dtype: float64
745 100
user_id
1      5.0
2      NaN
3      NaN
4      NaN
5      5.0
      ... 
939    NaN
940    3.0
941    NaN
942    NaN
943    NaN
Name: 100, Length: 943, dtype: float64
870 188
user_id
1      3.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943  

533 1016
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 1016, Length: 943, dtype: float64
130 125
user_id
1      3.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 125, Length: 943, dtype: float64
286 91
user_id
1      5.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 91, Length: 943, dtype: float64
169 234
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      2.0
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    3.0
Name: 234, Length: 943, dtype: float64
130 249
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 249, Length: 943, dtype: float64
669 56
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    5.0
941    NaN
942    NaN
943    NaN
Name: 

178 133
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 133, Length: 943, dtype: float64
117 758
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 758, Length: 943, dtype: float64
234 200
user_id
1      3.0
2      NaN
3      NaN
4      NaN
5      2.0
      ... 
939    NaN
940    3.0
941    NaN
942    4.0
943    NaN
Name: 200, Length: 943, dtype: float64
102 635
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 635, Length: 943, dtype: float64
182 763
user_id
1      NaN
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    3.0
942    NaN
943    NaN
Name: 763, Length: 943, dtype: float64
293 715
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 715, Lengt

334 265
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    5.0
943    NaN
Name: 265, Length: 943, dtype: float64
429 778
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 778, Length: 943, dtype: float64
620 151
user_id
1      4.0
2      NaN
3      NaN
4      NaN
5      3.0
      ... 
939    NaN
940    3.0
941    NaN
942    NaN
943    4.0
Name: 151, Length: 943, dtype: float64
478 340
user_id
1      NaN
2      NaN
3      5.0
4      NaN
5      NaN
      ... 
939    NaN
940    NaN
941    NaN
942    NaN
943    NaN
Name: 340, Length: 943, dtype: float64
85 488
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 488, Length: 943, dtype: float64
607 462
user_id
1     NaN
2     NaN
3     NaN
4     NaN
5     NaN
       ..
939   NaN
940   NaN
941   NaN
942   NaN
943   NaN
Name: 462, Length

1.0144591343876843

In [7]:
# practice 3-1 : using Pearson correlation coefficient

### Neighbor method

In [8]:
# RMSE with neighbor
def score(model, neighbor_size=0):
    id_pairs = zip(x_test['user_id'], x_test['movie_id'])
    y_pred = np.array([model(user, movie, neighbor_size) for (user, movie) in id_pairs])
    y_true = np.array(x_test['rating'])
    return RMSE(y_true, y_pred)

In [9]:
# getting prediction with fixed neightbor size
def cf_knn(user_id, movie_id, neighbor_size=0):
    if movie_id in rating_matrix:
        sim_scores = user_similarity[user_id].copy() # get similarity from user-user matrix
        movie_ratings = rating_matrix[movie_id].copy() # get rating from user-item matrix
        none_rating_idx = movie_ratings[movie_ratings.isnull()].index # list
        movie_ratings = movie_ratings.drop(none_rating_idx)
        sim_scores = sim_scores.drop(none_rating_idx)
        
        # if neighbor size is not fixed
        if neighbor_size == 0:
            mean_rating = np.dot(sim_scores, movie_ratings) / sim_scores.sum() # weighted average
        
        # if neighbor size is fixed
        else:
            if len(sim_scores) > 1:
                neighbor_size = min(neighbor_size, len(sim_scores))
                sim_scores = np.array(sim_scores)
                movie_ratings = np.array(movie_ratings)
                
                user_idx = np.argsort(sim_scores)
                sim_scores = sim_scores[user_idx][-neighbor_size:]
                movie_ratings = movie_ratings[user_idx][-neighbor_size:]
                mean_rating = np.dot(sim_scores, movie_ratings) / sim_scores.sum()
            else:
                mean_rating = 3.0
        
    else:
        mean_rating = 3.0
    
    return mean_rating

score(cf_knn, neighbor_size=30)            

1.0048621384539034

In [10]:
# Get full matrix and cosine similarity
rating_matrix = ratings.pivot_table(values='rating', index='user_id', columns='movie_id')
rating_matrix

movie_id  1     2     3     4     5     6     7     8     9     10    ...  \
user_id                                                               ...   
1          5.0   3.0   4.0   3.0   3.0   5.0   4.0   1.0   5.0   3.0  ...   
2          4.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   2.0  ...   
3          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
4          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
5          4.0   3.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
939        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   5.0   NaN  ...   
940        NaN   NaN   NaN   2.0   NaN   NaN   4.0   5.0   3.0   NaN  ...   
941        5.0   NaN   NaN   NaN   NaN   NaN   4.0   NaN   NaN   NaN  ...   
942        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
943        NaN   5.0   NaN   NaN   NaN   NaN   NaN   NaN   3.0   NaN  ...   

movie_id  1673  1674  1675  1676  1677  1678  1679  1680  1681  1682  
user_id                                                               
1          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
2          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
3          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
4          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
5          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
939        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
940        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
941        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
942        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
943        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  

[943 rows x 1682 columns]

In [11]:
dummy_matrix = rating_matrix.copy().fillna(0)
dummy_matrix

movie_id  1     2     3     4     5     6     7     8     9     10    ...  \
user_id                                                               ...   
1          5.0   3.0   4.0   3.0   3.0   5.0   4.0   1.0   5.0   3.0  ...   
2          4.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   2.0  ...   
3          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
4          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
5          4.0   3.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
939        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   5.0   0.0  ...   
940        0.0   0.0   0.0   2.0   0.0   0.0   4.0   5.0   3.0   0.0  ...   
941        5.0   0.0   0.0   0.0   0.0   0.0   4.0   0.0   0.0   0.0  ...   
942        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
943        0.0   5.0   0.0   0.0   0.0   0.0   0.0   0.0   3.0   0.0  ...   

movie_id  1673  1674  1675  1676  1677  1678  1679  1680  1681  1682  
user_id                                                               
1          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
2          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
3          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
4          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
5          0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
939        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
940        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
941        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
942        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
943        0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  

[943 rows x 1682 columns]

In [12]:
user_similarity = cosine_similarity(dummy_matrix, dummy_matrix)
user_similarity

array([[1.        , 0.16693098, 0.04745954, ..., 0.14861694, 0.17950788,
        0.39817474],
       [0.16693098, 1.        , 0.11059132, ..., 0.16148478, 0.17226781,
        0.10579788],
       [0.04745954, 0.11059132, 1.        , ..., 0.10124256, 0.13341615,
        0.02655587],
       ...,
       [0.14861694, 0.16148478, 0.10124256, ..., 1.        , 0.1016418 ,
        0.09511958],
       [0.17950788, 0.17226781, 0.13341615, ..., 0.1016418 , 1.        ,
        0.18246466],
       [0.39817474, 0.10579788, 0.02655587, ..., 0.09511958, 0.18246466,
        1.        ]])

In [13]:
user_similarity = pd.DataFrame(user_similarity, index=rating_matrix.index, columns=rating_matrix.index)
user_similarity

user_id       1         2         3         4         5         6         7    \
user_id                                                                         
1        1.000000  0.166931  0.047460  0.064358  0.378475  0.430239  0.440367   
2        0.166931  1.000000  0.110591  0.178121  0.072979  0.245843  0.107328   
3        0.047460  0.110591  1.000000  0.344151  0.021245  0.072415  0.066137   
4        0.064358  0.178121  0.344151  1.000000  0.031804  0.068044  0.091230   
5        0.378475  0.072979  0.021245  0.031804  1.000000  0.237286  0.373600   
...           ...       ...       ...       ...       ...       ...       ...   
939      0.118095  0.228583  0.026271  0.030138  0.071459  0.111852  0.107027   
940      0.314072  0.226790  0.161890  0.196858  0.239955  0.352449  0.329925   
941      0.148617  0.161485  0.101243  0.152041  0.139595  0.144446  0.059993   
942      0.179508  0.172268  0.133416  0.170086  0.152497  0.317328  0.282003   
943      0.398175  0.105798  0.026556  0.058752  0.313941  0.276042  0.394364   

user_id       8         9         10   ...       934       935       936  \
user_id                                ...                                 
1        0.319072  0.078138  0.376544  ...  0.369527  0.119482  0.274876   
2        0.103344  0.161048  0.159862  ...  0.156986  0.307942  0.358789   
3        0.083060  0.061040  0.065151  ...  0.031875  0.042753  0.163829   
4        0.188060  0.101284  0.060859  ...  0.052107  0.036784  0.133115   
5        0.248930  0.056847  0.201427  ...  0.338794  0.080580  0.094924   
...           ...       ...       ...  ...       ...       ...       ...   
939      0.095898  0.039852  0.071460  ...  0.066039  0.431154  0.258021   
940      0.246883  0.120495  0.342961  ...  0.327153  0.107024  0.187536   
941      0.146145  0.143245  0.090305  ...  0.046952  0.203301  0.288318   
942      0.175322  0.092497  0.212330  ...  0.226440  0.073513  0.089588   
943      0.299809  0.075617  0.221860  ...  0.263791  0.210763  0.143253   

user_id       937       938       939       940       941       942       943  
user_id                                                                        
1        0.189705  0.197326  0.118095  0.314072  0.148617  0.179508  0.398175  
2        0.424046  0.319889  0.228583  0.226790  0.161485  0.172268  0.105798  
3        0.069038  0.124245  0.026271  0.161890  0.101243  0.133416  0.026556  
4        0.193471  0.146058  0.030138  0.196858  0.152041  0.170086  0.058752  
5        0.079779  0.148607  0.071459  0.239955  0.139595  0.152497  0.313941  
...           ...       ...       ...       ...       ...       ...       ...  
939      0.226449  0.432666  1.000000  0.087687  0.180029  0.043264  0.144250  
940      0.181317  0.175158  0.087687  1.000000  0.145152  0.261376  0.241028  
941      0.234211  0.313400  0.180029  0.145152  1.000000  0.101642  0.095120  
942      0.129554  0.099385  0.043264  0.261376  0.101642  1.000000  0.182465  
943      0.077793  0.202244  0.144250  0.241028  0.095120  0.182465  1.000000  

[943 rows x 943 columns]

In [14]:
def recommend_movie_knn(user_id, n_items, neighbor_size=30):
    user_movie = rating_matrix.loc[user_id].copy()
    
    for movie in rating_matrix:
        # 이미 사용자가 평가한 영화의 경우 추천 대상에서 제외
        if pd.notnull(user_movie.loc[movie]):
            user_movie.loc[movie] = 0
        
        # 평가하지 않은 영화의 경우 cf_knn으로 예상 평점 계산
        else:
            user_movie.loc[movie] = cf_knn(user_id, movie, neighbor_size)
            
    movie_sort = user_movie.sort_values(ascending=False)[:n_items]
    recommend_movies = movies.loc[movie_sort.index]
    recommendations = recommend_movies['title']
    
    return recommendations

recommend_movie_knn(user_id=2, n_items=5, neighbor_size=30)

movie_id
1293                     Ayn Rand: A Sense of Life (1997)
1189                              That Old Feeling (1997)
1500    Prisoner of the Mountains (Kavkazsky Plennik) ...
1467                                     Cure, The (1995)
318                       Everyone Says I Love You (1996)
Name: title, dtype: object

### Decide optimal neighbor size

In [15]:
rating_matrix = x_train.pivot_table(values='rating', index='user_id', columns='movie_id')
dummy_matrix = rating_matrix.copy().fillna(0)
user_similarity = cosine_similarity(dummy_matrix, dummy_matrix)
user_similarity = pd.DataFrame(user_similarity, index=rating_matrix.index, columns=rating_matrix.index)

for neighbor_size in [10, 20, 30, 40, 50, 60]:
    print("Neighbor size = %d : RMSE = %.4f" % (neighbor_size, score(cf_knn, neighbor_size)))

Neighbor size = 10 : RMSE = 1.0202
Neighbor size = 20 : RMSE = 1.0066
Neighbor size = 30 : RMSE = 1.0049
Neighbor size = 40 : RMSE = 1.0051
Neighbor size = 50 : RMSE = 1.0059
Neighbor size = 60 : RMSE = 1.0065


### CF considering user bias

In [16]:
# rating mean of all user and rating deviation of movies
rating_mean = rating_matrix.mean(axis=1)
rating_bias = (rating_matrix.T - rating_mean).T

def cf_knn_bias(user_id, movie_id, neighbor_size=0):
    if movie_id in rating_bias:
        sim_scores = user_similarity[user_id].copy() # get similarity from user-user matrix
        movie_ratings = rating_bias[movie_id].copy() # get rating from user-item matrix
        none_rating_idx = movie_ratings[movie_ratings.isnull()].index # list
        movie_ratings = movie_ratings.drop(none_rating_idx)
        sim_scores = sim_scores.drop(none_rating_idx)
        
        # if neighbor size is not fixed
        if neighbor_size == 0:
            prediction = np.dot(sim_scores, movie_ratings) / sim_scores.sum() # weighted average
            prediction = prediction + rating_mean[user_id]
        
        # if neighbor size is fixed
        else:
            if len(sim_scores) > 1:
                neighbor_size = min(neighbor_size, len(sim_scores))
                sim_scores = np.array(sim_scores)
                movie_ratings = np.array(movie_ratings)
                
                user_idx = np.argsort(sim_scores)
                sim_scores = sim_scores[user_idx][-neighbor_size:]
                movie_ratings = movie_ratings[user_idx][-neighbor_size:]
                prediction = np.dot(sim_scores, movie_ratings) / sim_scores.sum()
                prediction = prediction + rating_mean[user_id]
            else:
                prediction = rating_mean[user_id]
        
    else:
        prediction = rating_mean[user_id]
    
    return prediction

score(cf_knn_bias, neighbor_size=30)  

0.9410787293111474

In [17]:
# practice 3-2 

### Other improving method of CF

In [18]:
# Significance weighting
rating_binary1 = np.array((rating_matrix > 0).astype(float))
rating_binary2 = rating_binary1.T

counts = np.dot(rating_binary1, rating_binary2)
counts = pd.DataFrame(counts, index=rating_matrix.index, columns=rating_matrix.index).fillna(0)

In [19]:
def cf_knn_bias_sig(user_id, movie_id, neighbor_size=0):
    if movie_id in rating_bias:
        sim_scores = user_similarity[user_id].copy() # get similarity from user-user matrix
        movie_ratings = rating_bias[movie_id].copy() # get rating from user-item matrix
        
        no_rating = movie_ratings.isnull()
        common_counts = counts[user_id]
        low_significance = common_counts < SIG_LEVEL
        none_rating_idx = movie_ratings[no_rating | low_significance].index # list
        movie_ratings = movie_ratings.drop(none_rating_idx)
        sim_scores = sim_scores.drop(none_rating_idx)
        
        # if neighbor size is not fixed
        if neighbor_size == 0:
            prediction = np.dot(sim_scores, movie_ratings) / sim_scores.sum() # weighted average
            prediction = prediction + rating_mean[user_id]
        
        # if neighbor size is fixed
        else:
            if len(sim_scores) > MIN_RATINGS:
                neighbor_size = min(neighbor_size, len(sim_scores))
                sim_scores = np.array(sim_scores)
                movie_ratings = np.array(movie_ratings)
                
                user_idx = np.argsort(sim_scores)
                sim_scores = sim_scores[user_idx][-neighbor_size:]
                movie_ratings = movie_ratings[user_idx][-neighbor_size:]
                prediction = np.dot(sim_scores, movie_ratings) / sim_scores.sum()
                prediction = prediction + rating_mean[user_id]
            else:
                prediction = rating_mean[user_id]
        
    else:
        prediction = rating_mean[user_id]
    
    return prediction

SIG_LEVEL = 3
MIN_RATINGS = 2
score(cf_knn_bias_sig, neighbor_size=30)

0.9408982130839146

In [20]:
# practice 3-3
def cf_knn_bias_sig_ctrl(user_id, movie_id, neighbor_size=0):
    if movie_id in rating_bias:
        sim_scores = user_similarity[user_id].copy() # get similarity from user-user matrix
        movie_ratings = rating_bias[movie_id].copy() # get rating from user-item matrix
        
        no_rating = movie_ratings.isnull()
        common_counts = counts[user_id]
        low_significance = common_counts < SIG_LEVEL
        none_rating_idx = movie_ratings[no_rating | low_significance].index # list
        movie_ratings = movie_ratings.drop(none_rating_idx)
        sim_scores = sim_scores.drop(none_rating_idx)
        
        # if neighbor size is not fixed
        if neighbor_size == 0:
            prediction = np.dot(sim_scores, movie_ratings) / sim_scores.sum() # weighted average
            prediction = prediction + rating_mean[user_id]
        
        # if neighbor size is fixed
        else:
            if len(sim_scores) > MIN_RATINGS:
                neighbor_size = min(neighbor_size, len(sim_scores))
                sim_scores = np.array(sim_scores)
                movie_ratings = np.array(movie_ratings)
                
                user_idx = np.argsort(sim_scores)
                sim_scores = sim_scores[user_idx][-neighbor_size:]
                movie_ratings = movie_ratings[user_idx][-neighbor_size:]
                prediction = np.dot(sim_scores, movie_ratings) / sim_scores.sum()
                prediction = prediction + rating_mean[user_id]
            else:
                prediction = rating_mean[user_id]
        
    else:
        prediction = rating_mean[user_id]
        
    if prediction < 1:
        prediction = 1
    elif prediction > 5:
        prediction = 5
    
    return prediction

SIG_LEVEL = 3
MIN_RATINGS = 2
score(cf_knn_bias_sig_ctrl, neighbor_size=30)

0.9397161617327524

### Item-based CF

In [21]:
# Item-based CF
from sklearn.metrics.pairwise import cosine_similarity

rating_matrix_t = np.transpose(rating_matrix)
dummy_matrix = rating_matrix_t.copy().fillna(0)

item_similarity = cosine_similarity(dummy_matrix, dummy_matrix)
item_similarity = pd.DataFrame(item_similarity, index=rating_matrix_t.index, columns=rating_matrix_t.index)
item_similarity

movie_id      1         2         3         4         5         6     \
movie_id                                                               
1         1.000000  0.323517  0.283064  0.337781  0.200973  0.114828   
2         0.323517  1.000000  0.237736  0.421471  0.216941  0.058497   
3         0.283064  0.237736  1.000000  0.245359  0.134361  0.107368   
4         0.337781  0.421471  0.245359  1.000000  0.202689  0.075810   
5         0.200973  0.216941  0.134361  0.202689  1.000000  0.018490   
...            ...       ...       ...       ...       ...       ...   
1672      0.038544  0.060169  0.000000  0.045486  0.000000  0.041667   
1674      0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
1675      0.000000  0.000000  0.000000  0.107211  0.000000  0.000000   
1680      0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
1682      0.054509  0.000000  0.109326  0.000000  0.117670  0.000000   

movie_id      7         8         9         10    ...      1664  1668  1669  \
movie_id                                          ...                         
1         0.443148  0.345230  0.392624  0.204043  ...  0.056933   0.0   0.0   
2         0.286661  0.263311  0.218417  0.156734  ...  0.039500   0.0   0.0   
3         0.270812  0.149354  0.236627  0.096356  ...  0.000000   0.0   0.0   
4         0.384975  0.395659  0.308195  0.210218  ...  0.000000   0.0   0.0   
5         0.241345  0.153276  0.191975  0.022140  ...  0.000000   0.0   0.0   
...            ...       ...       ...       ...  ...       ...   ...   ...   
1672      0.042038  0.067395  0.046145  0.063022  ...  0.000000   0.0   0.0   
1674      0.059450  0.095312  0.000000  0.000000  ...  0.000000   0.0   0.0   
1675      0.000000  0.076249  0.000000  0.089126  ...  0.000000   0.0   0.0   
1680      0.000000  0.000000  0.000000  0.000000  ...  0.000000   0.0   0.0   
1682      0.059450  0.000000  0.081574  0.000000  ...  0.000000   0.0   0.0   

movie_id  1670  1671      1672  1674      1675  1680      1682  
movie_id                                                        
1          0.0   0.0  0.038544   0.0  0.000000   0.0  0.054509  
2          0.0   0.0  0.060169   0.0  0.000000   0.0  0.000000  
3          0.0   0.0  0.000000   0.0  0.000000   0.0  0.109326  
4          0.0   0.0  0.045486   0.0  0.107211   0.0  0.000000  
5          0.0   0.0  0.000000   0.0  0.000000   0.0  0.117670  
...        ...   ...       ...   ...       ...   ...       ...  
1672       0.0   0.0  1.000000   0.0  0.000000   0.0  0.000000  
1674       0.0   0.0  0.000000   1.0  0.000000   0.0  0.000000  
1675       0.0   0.0  0.000000   0.0  1.000000   0.0  0.000000  
1680       0.0   0.0  0.000000   0.0  0.000000   1.0  0.000000  
1682       0.0   0.0  0.000000   0.0  0.000000   0.0  1.000000  

[1646 rows x 1646 columns]

In [22]:
def score(model):
    id_pairs = zip(x_test['user_id'], x_test['movie_id'])
    y_pred = np.array([model(user, movie) for (user, movie) in id_pairs])
    y_true = np.array(x_test['rating'])
    return RMSE(y_true, y_pred)

# compute (selected) movie_id weighted rating (weight = similarity)
def cf_ibcf(user_id, movie_id):
    if movie_id in item_similarity:
        sim_scores = item_similarity[movie_id]
        user_rating = rating_matrix_t[user_id]
        non_rating_idx = user_rating[user_rating.isnull()].index
        user_rating = user_rating.dropna()
        sim_scores = sim_scores.drop(non_rating_idx)
        mean_rating = np.dot(sim_scores, user_rating) / sim_scores.sum()
    else:
        mean_rating = 3.0
    
    return mean_rating

score(cf_ibcf)

1.0174814310922347

### Recommender system metrics

In [ ]:
# for explicit data
## MAD(Mean Absolute Deviation)
## MSE(Mean Squared Error)
## RMSE (Root Mean Square Error)

# for binary(success, fail) data
## accuracy
## precision
## recall
## F1 score
## coverage